Домашнее задание (часть 1)
1. взять любой набор данных для бинарной классификации (можно скачать один из модельных с https://archive.ics.uci.edu/ml/datasets.php)
2. сделать eda (как на занятии 6 с примером для оттока)
3. сделать feature engineering
4. обучить любой классификатор (какой вам нравится)
5. далее разделить ваш набор данных на два множества: P (positives) и U (unlabeled). Причем брать нужно не все  положительные (класс 1) примеры, а только лишь часть
6. применить random negative sampling для построения классификатора в новых условиях
7. сравнить качество с решением из пункта 4 (построить отчет - таблицу метрик)

In [1]:
#Importing libraries
import numpy as np # linear algebra
import pandas as pd # data processing, CSV file I/O (e.g. pd.read_csv)
# Input data files are available in the "../input/" directory.
import os
import matplotlib.pyplot as plt#visualization
from PIL import Image
%matplotlib inline
import pandas as pd
import seaborn as sns#visualization
import itertools
import warnings
warnings.filterwarnings("ignore")
import io
import plotly
import plotly.offline as py#visualization
py.init_notebook_mode(connected=True)#visualization
import plotly.graph_objs as go#visualization
import plotly.tools as tls#visualization
import plotly.figure_factory as ff#visualization

In [2]:
ds_name="adult.data"
data = pd.read_csv(ds_name, header=None)

**Prediction task is to determine whether a person makes over 50K a year.**

In [3]:
print(data.shape)
data.head(10)

(32561, 15)


0                  1       2           3   4                       5   \
0  39          State-gov   77516   Bachelors  13           Never-married   
1  50   Self-emp-not-inc   83311   Bachelors  13      Married-civ-spouse   
2  38            Private  215646     HS-grad   9                Divorced   
3  53            Private  234721        11th   7      Married-civ-spouse   
4  28            Private  338409   Bachelors  13      Married-civ-spouse   
5  37            Private  284582     Masters  14      Married-civ-spouse   
6  49            Private  160187         9th   5   Married-spouse-absent   
7  52   Self-emp-not-inc  209642     HS-grad   9      Married-civ-spouse   
8  31            Private   45781     Masters  14           Never-married   
9  42            Private  159449   Bachelors  13      Married-civ-spouse   

                   6               7       8        9      10  11  12  \
0        Adm-clerical   Not-in-family   White     Male   2174   0  40   
1     Exec-managerial         Husband   White     Male      0   0  13   
2   Handlers-cleaners   Not-in-family   White     Male      0   0  40   
3   Handlers-cleaners         Husband   Black     Male      0   0  40   
4      Prof-specialty            Wife   Black   Female      0   0  40   
5     Exec-managerial            Wife   White   Female      0   0  40   
6       Other-service   Not-in-family   Black   Female      0   0  16   
7     Exec-managerial         Husband   White     Male      0   0  45   
8      Prof-specialty   Not-in-family   White   Female  14084   0  50   
9     Exec-managerial         Husband   White     Male   5178   0  40   

               13      14  
0   United-States   <=50K  
1   United-States   <=50K  
2   United-States   <=50K  
3   United-States   <=50K  
4            Cuba   <=50K  
5   United-States   <=50K  
6         Jamaica   <=50K  
7   United-States    >50K  
8   United-States    >50K  
9   United-States    >50K

In [4]:
data.iloc[:, -1].value_counts()

 <=50K    24720
 >50K      7841
Name: 14, dtype: int64

**1 - соответствует >50K**

**0 - соответствует <=50K**

In [5]:
data.loc[data[14]==" <=50K",14]=0

In [6]:
data.loc[data[14]==" >50K",14]=1

In [7]:
data.iloc[:, -1].value_counts()

0    24720
1     7841
Name: 14, dtype: int64

**EDA**

In [8]:
data.columns=['age','workclass','fnlwgt','education','education-num','marital-status','occupation','relationship','race','sex','capital-gain','capital-loss','hours-per-week','native-country','income']

In [9]:

print(data.describe())

                age        fnlwgt  education-num  capital-gain  capital-loss  \
count  32561.000000  3.256100e+04   32561.000000  32561.000000  32561.000000   
mean      38.581647  1.897784e+05      10.080679   1077.648844     87.303830   
std       13.640433  1.055500e+05       2.572720   7385.292085    402.960219   
min       17.000000  1.228500e+04       1.000000      0.000000      0.000000   
25%       28.000000  1.178270e+05       9.000000      0.000000      0.000000   
50%       37.000000  1.783560e+05      10.000000      0.000000      0.000000   
75%       48.000000  2.370510e+05      12.000000      0.000000      0.000000   
max       90.000000  1.484705e+06      16.000000  99999.000000   4356.000000   

       hours-per-week  
count    32561.000000  
mean        40.437456  
std         12.347429  
min          1.000000  
25%         40.000000  
50%         40.000000  
75%         45.000000  
max         99.000000  


In [10]:
print ("Rows     : " ,data.shape[0])
print ("Columns  : " ,data.shape[1])
print ("\nFeatures : \n" ,data.columns.tolist())
print ("\nMissing values :  ", data.isnull().sum().values.sum())
print ("\nUnique values :  \n",data.nunique())

print(data.iloc[:, -1].isnull().sum())

Rows     :  32561
Columns  :  15

Features : 
 ['age', 'workclass', 'fnlwgt', 'education', 'education-num', 'marital-status', 'occupation', 'relationship', 'race', 'sex', 'capital-gain', 'capital-loss', 'hours-per-week', 'native-country', 'income']

Missing values :   0

Unique values :  
 age                  73
workclass             9
fnlwgt            21648
education            16
education-num        16
marital-status        7
occupation           15
relationship          6
race                  5
sex                   2
capital-gain        119
capital-loss         92
hours-per-week       94
native-country       42
income                2
dtype: int64
0


In [11]:
data.head(10)

age          workclass  fnlwgt   education  education-num  \
0   39          State-gov   77516   Bachelors             13   
1   50   Self-emp-not-inc   83311   Bachelors             13   
2   38            Private  215646     HS-grad              9   
3   53            Private  234721        11th              7   
4   28            Private  338409   Bachelors             13   
5   37            Private  284582     Masters             14   
6   49            Private  160187         9th              5   
7   52   Self-emp-not-inc  209642     HS-grad              9   
8   31            Private   45781     Masters             14   
9   42            Private  159449   Bachelors             13   

           marital-status          occupation    relationship    race  \
0           Never-married        Adm-clerical   Not-in-family   White   
1      Married-civ-spouse     Exec-managerial         Husband   White   
2                Divorced   Handlers-cleaners   Not-in-family   White   
3      Married-civ-spouse   Handlers-cleaners         Husband   Black   
4      Married-civ-spouse      Prof-specialty            Wife   Black   
5      Married-civ-spouse     Exec-managerial            Wife   White   
6   Married-spouse-absent       Other-service   Not-in-family   Black   
7      Married-civ-spouse     Exec-managerial         Husband   White   
8           Never-married      Prof-specialty   Not-in-family   White   
9      Married-civ-spouse     Exec-managerial         Husband   White   

       sex  capital-gain  capital-loss  hours-per-week  native-country income  
0     Male          2174             0              40   United-States      0  
1     Male             0             0              13   United-States      0  
2     Male             0             0              40   United-States      0  
3     Male             0             0              40   United-States      0  
4   Female             0             0              40            Cuba      0  
5   Female             0             0              40   United-States      0  
6   Female             0             0              16         Jamaica      0  
7     Male             0             0              45   United-States      1  
8   Female         14084             0              50   United-States      1  
9     Male          5178             0              40   United-States      1

In [12]:
#labels
lab = data['income'].value_counts().keys().tolist()
#values
val = data['income'].value_counts().values.tolist()

trace = go.Pie(labels = lab ,
               values = val ,
               marker = dict(colors =  [ 'royalblue' ,'lime'],
                             line = dict(color = "white",
                                         width =  1.3)
                            ),
               rotation = 90,
               hoverinfo = "label+value+text",
               hole = .5
              )
layout = go.Layout(dict(title = "Income >50K : 1,<=50K : 0 in data",
                        plot_bgcolor  = "rgb(243,243,243)",
                        paper_bgcolor = "rgb(243,243,243)",
                       )
                  )

fig_data = [trace]
fig = go.Figure(data = fig_data,layout = layout)
py.iplot(fig)

In [13]:
#пропуски и пустые строки
print(data[((data['fnlwgt']==' ') | (data['fnlwgt'].isnull()))]['fnlwgt'].values.sum())
print(len(data[data["fnlwgt"].notnull()]))
print(data[((data['age']==' ') | (data['age'].isnull()))]['age'].values.sum())
print(len(data[data["age"].notnull()]))
print(data[((data['education-num']==' ') | (data['education-num'].isnull()))]['education-num'].values.sum())
print(len(data[data["education-num"].notnull()]))
print(data[((data['capital-gain']==' ') | (data['capital-gain'].isnull()))]['capital-gain'].values.sum())
print(len(data[data["capital-gain"].notnull()]))
print(data[((data['capital-loss']==' ') | (data['capital-loss'].isnull()))]['capital-loss'].values.sum())
print(len(data[data["capital-loss"].notnull()]))
print(data[((data['hours-per-week']==' ') | (data['hours-per-week'].isnull()))]['hours-per-week'].values.sum())
print(len(data[data["hours-per-week"].notnull()]))

0
32561
0
32561
0
32561
0
32561
0
32561
0
32561


**Пропусков и пустых строк нет среди некатегориальных полей**

**Преобразуем в категориальные поля некоторые поля**

In [14]:
#age to categorical column
def age_lab(data) :
    
    if data["age"] <= 20 :
        return "age_17-20"
    elif (data["age"] > 20) & (data["age"] <= 25 ):
        return "age_20-25"
    elif (data["age"] > 25) & (data["age"] <= 30) :
        return "age_25-30"
    elif (data["age"] > 30) & (data["age"] <= 40) :
        return "age_30-40"
    elif (data["age"] > 40) & (data["age"] <= 50) :
        return "age_40-50"
    elif (data["age"] > 50) & (data["age"] <= 60) :
        return "age_50-60"
    elif data["age"] > 60 :
        return "age_gt_60"
    
data["age_group"] = data.apply(lambda data:age_lab(data), axis = 1)
    
#education-num нужно убрать - он лишний, т.к. он дублирует категориальный столбец education и совпадает с ним по количеству
# уникальных столбцов
data = data.drop(columns = ['education-num'],axis = 1)


In [15]:

print('capital-gain==0,count=',data[data['capital-gain']==0]['capital-gain'].count())
print('capital-gain>0,count=',data[data['capital-gain']>0]['capital-gain'].count())

capital-gain==0,count= 29849
capital-gain>0,count= 2712


In [16]:
print('capital-gain 0-1000,count=',data[((data['capital-gain']>0) & (data['capital-gain']<=1000))]['capital-gain'].count())
print('capital-gain 1000-2000,count=',data[((data['capital-gain']>1000) & (data['capital-gain']<=2000))]['capital-gain'].count())
print('capital-gain 2000-3000,count=',data[((data['capital-gain']>2000) & (data['capital-gain']<=3000))]['capital-gain'].count())
print('capital-gain 3000-4000,count=',data[((data['capital-gain']>3000) & (data['capital-gain']<=4000))]['capital-gain'].count())
print('capital-gain 4000-5000,count=',data[((data['capital-gain']>4000) & (data['capital-gain']<=5000))]['capital-gain'].count())
print('capital-gain 5000-6000,count=',data[((data['capital-gain']>5000) & (data['capital-gain']<=6000))]['capital-gain'].count())
print('capital-gain 6000-7000,count=',data[((data['capital-gain']>6000) & (data['capital-gain']<=7000))]['capital-gain'].count())
print('capital-gain 7000-8000,count=',data[((data['capital-gain']>7000) & (data['capital-gain']<=8000))]['capital-gain'].count())
print('capital-gain 8000-9000,count=',data[((data['capital-gain']>8000) & (data['capital-gain']<=9000))]['capital-gain'].count())
print('capital-gain 9000-10000,count=',data[((data['capital-gain']>9000) & (data['capital-gain']<=10000))]['capital-gain'].count())
print('capital-gain 10000-14000,count=',data[((data['capital-gain']>10000) & (data['capital-gain']<=14000))]['capital-gain'].count())
print('capital-gain 14000-16000,count=',data[((data['capital-gain']>14000) & (data['capital-gain']<=16000))]['capital-gain'].count())
print('capital-gain >16000,count=',data[((data['capital-gain']>16000))]['capital-gain'].count())


capital-gain 0-1000,count= 55
capital-gain 1000-2000,count= 95
capital-gain 2000-3000,count= 322
capital-gain 3000-4000,count= 344
capital-gain 4000-5000,count= 248
capital-gain 5000-6000,count= 186
capital-gain 6000-7000,count= 63
capital-gain 7000-8000,count= 548
capital-gain 8000-9000,count= 55
capital-gain 9000-10000,count= 26
capital-gain 10000-14000,count= 90
capital-gain 14000-16000,count= 425
capital-gain >16000,count= 255


In [17]:
#capital-gain to categorical column
def capital_gain_lab(data) :
    
    if data["capital-gain"] == 0 :
        return "capital-gain_0"
    elif (data["capital-gain"] > 0) & (data["capital-gain"] <= 2000 ):
        return "capital-gain_1-2000"
    elif (data["capital-gain"] > 2000) & (data["capital-gain"] <= 3000) :
        return "capital-gain_2001-3000"
    elif (data["capital-gain"] > 3000) & (data["capital-gain"] <= 4000) :
        return "capital-gain_3001-4000"
    elif (data["capital-gain"] > 4000) & (data["capital-gain"] <= 5000) :
        return "capital-gain_4001-5000"
    elif (data["capital-gain"] > 5000) & (data["capital-gain"] <= 7000) :
        return "capital-gain_5001-7000"
    elif (data["capital-gain"] > 7000) & (data["capital-gain"] <= 8000) :
        return "capital-gain_7001-8000"
    elif (data["capital-gain"] > 8000) & (data["capital-gain"] <= 14000) :
        return "capital-gain_8001-14000"
    elif (data["capital-gain"] > 14000) & (data["capital-gain"] <= 16000) :
        return "capital-gain_14001-16000"
    elif data["capital-gain"] > 16000 :
        return "capital-gain_gt_16000"
    
data["capital-gain_group"] = data.apply(lambda data:capital_gain_lab(data), axis = 1)

In [18]:
print('capital-loss==0,count=',data[data['capital-loss']==0]['capital-loss'].count())
print('capital-loss>0,count=',data[data['capital-loss']>0]['capital-loss'].count())

capital-loss==0,count= 31042
capital-loss>0,count= 1519


In [19]:
print('capital-loss 0-1600,count=',data[((data['capital-loss']>0) & (data['capital-loss']<=1600))]['capital-loss'].count())
print('capital-loss 1600-1800,count=',data[((data['capital-loss']>1600) & (data['capital-loss']<=1800))]['capital-loss'].count())
print('capital-loss 1800-1900,count=',data[((data['capital-loss']>1800) & (data['capital-loss']<=1900))]['capital-loss'].count())
print('capital-loss 1900-2000,count=',data[((data['capital-loss']>1900) & (data['capital-loss']<=2000))]['capital-loss'].count())
print('capital-loss 2000-3000,count=',data[((data['capital-loss']>2000) & (data['capital-loss']<=3000))]['capital-loss'].count())
print('capital-loss >3000,count=',data[((data['capital-loss']>3000) )]['capital-loss'].count())


capital-loss 0-1600,count= 254
capital-loss 1600-1800,count= 272
capital-loss 1800-1900,count= 256
capital-loss 1900-2000,count= 412
capital-loss 2000-3000,count= 314
capital-loss >3000,count= 11


In [20]:
#capital-loss to categorical column
def capital_loss_lab(data) :
    
    if data["capital-loss"] == 0 :
        return "capital-loss_0"
    elif (data["capital-loss"] > 0) & (data["capital-loss"] <= 1600 ):
        return "capital-loss_1-1600"
    elif (data["capital-loss"] > 1600) & (data["capital-loss"] <= 1800) :
        return "capital-loss_1601-1800"
    elif (data["capital-loss"] > 1800) & (data["capital-loss"] <= 1900) :
        return "capital-loss_1801-1900"
    elif (data["capital-loss"] > 1900) & (data["capital-loss"] <= 2000) :
        return "capital-loss_1901-2000"
    elif (data["capital-loss"] > 2000) & (data["capital-loss"] <= 3000) :
        return "capital-loss_2001-3000"
    elif (data["capital-loss"] > 3000) :
        return "capital-loss_gt_3000"
    
data["capital-loss_group"] = data.apply(lambda data:capital_loss_lab(data), axis = 1)

In [21]:
print('hours-per-week 1-20,count=',data[((data['hours-per-week']>=1) & (data['hours-per-week']<=20))]['hours-per-week'].count())
print('hours-per-week 20-30,count=',data[((data['hours-per-week']>20) & (data['hours-per-week']<=30))]['hours-per-week'].count())
print('hours-per-week 30-38,count=',data[((data['hours-per-week']>30) & (data['hours-per-week']<=38))]['hours-per-week'].count())
print('hours-per-week 38-40,count=',data[((data['hours-per-week']>38) & (data['hours-per-week']<=40))]['hours-per-week'].count())
print('hours-per-week 40-45,count=',data[((data['hours-per-week']>40) & (data['hours-per-week']<=45))]['hours-per-week'].count())
print('hours-per-week 45-50,count=',data[((data['hours-per-week']>45) & (data['hours-per-week']<=50))]['hours-per-week'].count())
print('hours-per-week 50-60,count=',data[((data['hours-per-week']>50) & (data['hours-per-week']<=60))]['hours-per-week'].count())
print('hours-per-week >60,count=',data[((data['hours-per-week']>60))]['hours-per-week'].count())


hours-per-week 1-20,count= 2928
hours-per-week 20-30,count= 2317
hours-per-week 30-38,count= 2480
hours-per-week 38-40,count= 15255
hours-per-week 40-45,count= 2442
hours-per-week 45-50,count= 3496
hours-per-week 50-60,count= 2533
hours-per-week >60,count= 1110


In [22]:
#hours-per-week to categorical column
def hours_per_week_lab(data) :   
    
    if (data["hours-per-week"] >= 1) & (data["hours-per-week"] <= 20 ):
        return "hours-per-week_1-20"
    elif (data["hours-per-week"] > 20) & (data["hours-per-week"] <= 30) :
        return "hours-per-week_21-30"
    elif (data["hours-per-week"] > 30) & (data["hours-per-week"] <= 38) :
        return "hours-per-week_31-38"
    elif (data["hours-per-week"] > 38) & (data["hours-per-week"] <= 40) :
        return "hours-per-week_39-40"
    elif (data["hours-per-week"] > 40) & (data["hours-per-week"] <= 45) :
        return "hours-per-week_41-45" 
    elif (data["hours-per-week"] > 45) & (data["hours-per-week"] <= 50) :
        return "hours-per-week_46-50"
    elif (data["hours-per-week"] > 50) & (data["hours-per-week"] <= 60) :
        return "hours-per-week_51-60"
    elif (data["hours-per-week"] > 60) :
        return "hours-per-week_gt_60"
    
data["hours-per-week_group"] = data.apply(lambda data:hours_per_week_lab(data), axis = 1)

In [23]:
data.head()

age          workclass  fnlwgt   education       marital-status  \
0   39          State-gov   77516   Bachelors        Never-married   
1   50   Self-emp-not-inc   83311   Bachelors   Married-civ-spouse   
2   38            Private  215646     HS-grad             Divorced   
3   53            Private  234721        11th   Married-civ-spouse   
4   28            Private  338409   Bachelors   Married-civ-spouse   

           occupation    relationship    race      sex  capital-gain  \
0        Adm-clerical   Not-in-family   White     Male          2174   
1     Exec-managerial         Husband   White     Male             0   
2   Handlers-cleaners   Not-in-family   White     Male             0   
3   Handlers-cleaners         Husband   Black     Male             0   
4      Prof-specialty            Wife   Black   Female             0   

   capital-loss  hours-per-week  native-country income  age_group  \
0             0              40   United-States      0  age_30-40   
1             0              13   United-States      0  age_40-50   
2             0              40   United-States      0  age_30-40   
3             0              40   United-States      0  age_50-60   
4             0              40            Cuba      0  age_25-30   

       capital-gain_group capital-loss_group  hours-per-week_group  
0  capital-gain_2001-3000     capital-loss_0  hours-per-week_39-40  
1          capital-gain_0     capital-loss_0   hours-per-week_1-20  
2          capital-gain_0     capital-loss_0  hours-per-week_39-40  
3          capital-gain_0     capital-loss_0  hours-per-week_39-40  
4          capital-gain_0     capital-loss_0  hours-per-week_39-40

In [24]:
print ("\nUnique values :  \n",data.nunique())


Unique values :  
 age                        73
workclass                   9
fnlwgt                  21648
education                  16
marital-status              7
occupation                 15
relationship                6
race                        5
sex                         2
capital-gain              119
capital-loss               92
hours-per-week             94
native-country             42
income                      2
age_group                   7
capital-gain_group         10
capital-loss_group          7
hours-per-week_group        8
dtype: int64


In [25]:
target_col = ["income"]
cat_cols   = data.nunique()[data.nunique() < 50].keys().tolist()
cat_cols   = [x for x in cat_cols if x not in target_col]
num_cols   = [x for x in data.columns if x not in cat_cols + target_col]

In [26]:
#Separating income > 50K and  income <=50K 
income_gt_50K = data[data["income"] == 1]
income_lq_50K = data[data["income"] == 0]

In [27]:
#function  for pie plot for customer attrition types
def plot_pie(column) :
    
    trace1 = go.Pie(values  = income_gt_50K[column].value_counts().values.tolist(),
                    labels  = income_gt_50K[column].value_counts().keys().tolist(),
                    hoverinfo = "label+percent+name",
                    domain  = dict(x = [0,.48]),
                    name    = "income > 50K clients",
                    marker  = dict(line = dict(width = 2,
                                               color = "rgb(243,243,243)")
                                  ),
                    hole    = .6
                   )
    trace2 = go.Pie(values  = income_lq_50K[column].value_counts().values.tolist(),
                    labels  = income_lq_50K[column].value_counts().keys().tolist(),
                    hoverinfo = "label+percent+name",
                    marker  = dict(line = dict(width = 2,
                                               color = "rgb(243,243,243)")
                                  ),
                    domain  = dict(x = [.52,1]),
                    hole    = .6,
                    name    = "income <= 50K clients" 
                   )


    layout = go.Layout(dict(title = column + " distribution in customers ",
                            plot_bgcolor  = "rgb(243,243,243)",
                            paper_bgcolor = "rgb(243,243,243)",
                            annotations = [dict(text = "income > 50K clients",
                                                font = dict(size = 13),
                                                showarrow = False,
                                                x = .15, y = .5),
                                           dict(text = "income <= 50K clients",
                                                font = dict(size = 13),
                                                showarrow = False,
                                                x = .88,y = .5
                                               )
                                          ]
                           )
                      )
    data_fig = [trace1,trace2]
    fig  = go.Figure(data = data_fig,layout = layout)
    py.iplot(fig)


#function  for histogram for customer attrition types
def histogram(column) :
    trace1 = go.Histogram(x  = income_gt_50K[column],
                          histnorm= "percent",
                          name = "income > 50K clients",
                          marker = dict(line = dict(width = .5,
                                                    color = "black"
                                                    )
                                        ),
                         opacity = .9 
                         ) 
    
    trace2 = go.Histogram(x  = income_lq_50K[column],
                          histnorm = "percent",
                          name = "income <= 50K clients",
                          marker = dict(line = dict(width = .5,
                                              color = "black"
                                             )
                                 ),
                          opacity = .9
                         )
    
    data_fig = [trace1,trace2]
    layout = go.Layout(dict(title =column + " distribution in customers ",
                            plot_bgcolor  = "rgb(243,243,243)",
                            paper_bgcolor = "rgb(243,243,243)",
                            xaxis = dict(gridcolor = 'rgb(255, 255, 255)',
                                             title = column,
                                             zerolinewidth=1,
                                             ticklen=5,
                                             gridwidth=2
                                            ),
                            yaxis = dict(gridcolor = 'rgb(255, 255, 255)',
                                             title = "percent",
                                             zerolinewidth=1,
                                             ticklen=5,
                                             gridwidth=2
                                            ),
                           )
                      )
    fig  = go.Figure(data=data_fig,layout=layout)
    
    py.iplot(fig)
    
#function  for scatter plot matrix  for numerical columns in data_fig
def scatter_matrix(df)  :
    
    df  = df.sort_values(by = "income" ,ascending = True)
    classes = df["income"].unique().tolist()
    classes
    
    class_code  = {classes[k] : k for k in range(2)}
    class_code

    color_vals = [class_code[cl] for cl in df["income"]]
    color_vals

    pl_colorscale = "Portland"

    pl_colorscale

    text = [df.loc[k,"income"] for k in range(len(df))]
    text

    trace = go.Splom(dimensions = [dict(label  = "age",
                                       values = df["age"]),
                                  dict(label  = 'fnlwgt',
                                       values = df['fnlwgt']),
                                  dict(label  = 'capital-gain',
                                       values = df['capital-gain']),
                                  dict(label  = 'capital-loss',
                                       values = df['capital-loss']),
                                  dict(label  = 'hours-per-week',
                                       values = df['hours-per-week'])],
                     text = text,
                     marker = dict(color = color_vals,
                                   colorscale = pl_colorscale,
                                   size = 5,
                                   showscale = False,
                                   line = dict(width = .1,
                                               color='rgb(230,230,230)'
                                              )
                                  )
                    )
    axis = dict(showline  = True,
                zeroline  = False,
                gridcolor = "#fff",
                ticklen   = 4
               )
    
    layout = go.Layout(dict(title  = 
                            "Scatter plot matrix for Numerical columns for customers",
                            autosize = False,
                            height = 800,
                            width  = 800,
                            dragmode = "select",
                            hovermode = "closest",
                            plot_bgcolor  = 'rgba(240,240,240, 0.95)',
                            xaxis1 = dict(axis),
                            yaxis1 = dict(axis),
                            xaxis2 = dict(axis),
                            yaxis2 = dict(axis),
                            xaxis3 = dict(axis),
                            yaxis3 = dict(axis),
                           )
                      )
    data_fig   = [trace]
    fig = go.Figure(data = data_fig,layout = layout )
    py.iplot(fig)

#for all categorical columns plot pie
for i in cat_cols :
    plot_pie(i)

#for all categorical columns plot histogram    
for i in num_cols :
    histogram(i)

#scatter plot matrix
scatter_matrix(data)

In [28]:
#cusomer distribution in groups


group_cols=["age_group","capital-gain_group","capital-loss_group","hours-per-week_group"]
groups_gt_50Ks  = [income_gt_50K["age_group"].value_counts().reset_index(),
                   income_gt_50K["capital-gain_group"].value_counts().reset_index(),
                   income_gt_50K["capital-loss_group"].value_counts().reset_index(),
                   income_gt_50K["hours-per-week_group"].value_counts().reset_index()]
groups_lq_50Ks =  [income_lq_50K["age_group"].value_counts().reset_index(),
                   income_lq_50K["capital-gain_group"].value_counts().reset_index(),
                   income_lq_50K["capital-loss_group"].value_counts().reset_index(),
                   income_lq_50K["hours-per-week_group"].value_counts().reset_index()]
group_count=len(group_cols)

for i in range(group_count):
    groups_gt_50K=groups_gt_50Ks[i]
    groups_lq_50K=groups_lq_50Ks[i]
    groups_gt_50K.columns  = [group_cols[i],"count"]
    groups_lq_50K.columns = [group_cols[i],"count"]

    #bar - income_gt_50K
    trace1 = go.Bar(x = groups_gt_50K[group_cols[i]]  , y = groups_gt_50K["count"],
                name = "income > 50K Customers",
                marker = dict(line = dict(width = .5,color = "black")),
                opacity = .9)

    #bar - not income_gt_50K
    trace2 = go.Bar(x = groups_lq_50K[group_cols[i]] , y = groups_lq_50K["count"],
                name = "income <= 50K Customers",
                marker = dict(line = dict(width = .5,color = "black")),
                opacity = .9)

    layout = go.Layout(dict(title = "Customer distribution in "+group_cols[i],
                        plot_bgcolor  = "rgb(243,243,243)",
                        paper_bgcolor = "rgb(243,243,243)",
                        xaxis = dict(gridcolor = 'rgb(255, 255, 255)',
                                     title = group_cols[i],
                                     zerolinewidth=1,ticklen=5,gridwidth=2),
                        yaxis = dict(gridcolor = 'rgb(255, 255, 255)',
                                     title = "count",
                                     zerolinewidth=1,ticklen=5,gridwidth=2),
                       )
                  )
    data_fig = [trace1,trace2]
    fig  = go.Figure(data=data_fig,layout=layout)
    py.iplot(fig)

In [29]:
##copy data
data_df = data.copy()

### Data preprocessing

In [30]:
from sklearn.preprocessing import LabelEncoder
from sklearn.preprocessing import StandardScaler

bin_cols = data.nunique()[data.nunique() == 2].keys().tolist()
multi_cols = [i for i in cat_cols if i not in bin_cols]

#Label encoding Binary columns
le = LabelEncoder()
for i in bin_cols :
    data[i] = le.fit_transform(data[i])
    
#Duplicating columns for multi value columns
data = pd.get_dummies(data = data,columns = multi_cols )

#Scaling Numerical columns
std = StandardScaler()
scaled = std.fit_transform(data[num_cols])
scaled = pd.DataFrame(scaled,columns=num_cols)

#dropping original values merging scaled values for numerical columns
df_data_og = data.copy()
data = data.drop(columns = num_cols,axis = 1)
data = data.merge(scaled,left_index=True,right_index=True,how = "left")



In [31]:
summary = (df_data_og[[i for i in df_data_og.columns]].
           describe().transpose().reset_index())

summary = summary.rename(columns = {"index" : "feature"})
summary = np.around(summary,3)

val_lst = [summary['feature'], summary['count'],
           summary['mean'],summary['std'],
           summary['min'], summary['25%'],
           summary['50%'], summary['75%'], summary['max']]

trace  = go.Table(header = dict(values = summary.columns.tolist(),
                                line = dict(color = ['#506784']),
                                fill = dict(color = ['#119DFF']),
                               ),
                  cells  = dict(values = val_lst,
                                line = dict(color = ['#506784']),
                                fill = dict(color = ["lightgrey",'#F5F8FF'])
                               ),
                  columnwidth = [200,60,100,100,60,60,80,80,80])
layout = go.Layout(dict(title = "Variable Summary"))
figure = go.Figure(data=[trace],layout=layout)
py.iplot(figure)

In [32]:
#correlation
correlation = data.corr()
#tick labels
matrix_cols = correlation.columns.tolist()
#convert to array
corr_array  = np.array(correlation)

#Plotting
trace = go.Heatmap(z = corr_array,
                   x = matrix_cols,
                   y = matrix_cols,
                   colorscale = "Viridis",
                   colorbar   = dict(title = "Pearson Correlation coefficient",
                                     titleside = "right"
                                    ) ,
                  )

layout = go.Layout(dict(title = "Correlation Matrix for variables",
                        autosize = False,
                        height  = 720,
                        width   = 800,
                        margin  = dict(r = 0 ,l = 210,
                                       t = 25,b = 210,
                                      ),
                        yaxis   = dict(tickfont = dict(size = 9)),
                        xaxis   = dict(tickfont = dict(size = 9))
                       )
                  )

data_fig = [trace]
fig = go.Figure(data=data_fig,layout=layout)
py.iplot(fig)

In [33]:
data.head()

sex  income  workclass_ ?  workclass_ Federal-gov  workclass_ Local-gov  \
0    1       0             0                       0                     0   
1    1       0             0                       0                     0   
2    1       0             0                       0                     0   
3    1       0             0                       0                     0   
4    0       0             0                       0                     0   

   workclass_ Never-worked  workclass_ Private  workclass_ Self-emp-inc  \
0                        0                   0                        0   
1                        0                   0                        0   
2                        0                   1                        0   
3                        0                   1                        0   
4                        0                   1                        0   

   workclass_ Self-emp-not-inc  workclass_ State-gov  ...  \
0                            0                     1  ...   
1                            1                     0  ...   
2                            0                     0  ...   
3                            0                     0  ...   
4                            0                     0  ...   

   hours-per-week_group_hours-per-week_39-40  \
0                                          1   
1                                          0   
2                                          1   
3                                          1   
4                                          1   

   hours-per-week_group_hours-per-week_41-45  \
0                                          0   
1                                          0   
2                                          0   
3                                          0   
4                                          0   

   hours-per-week_group_hours-per-week_46-50  \
0                                          0   
1                                          0   
2                                          0   
3                                          0   
4                                          0   

   hours-per-week_group_hours-per-week_51-60  \
0                                          0   
1                                          0   
2                                          0   
3                                          0   
4                                          0   

   hours-per-week_group_hours-per-week_gt_60       age    fnlwgt  \
0                                          0  0.030671 -1.063611   
1                                          0  0.837109 -1.008707   
2                                          0 -0.042642  0.245079   
3                                          0  1.057047  0.425801   
4                                          0 -0.775768  1.408176   

   capital-gain  capital-loss  hours-per-week  
0      0.148453      -0.21666       -0.035429  
1     -0.145920      -0.21666       -2.222153  
2     -0.145920      -0.21666       -0.035429  
3     -0.145920      -0.21666       -0.035429  
4     -0.145920      -0.21666       -0.035429  

[5 rows x 139 columns]

In [34]:
from sklearn.model_selection import train_test_split

cols = [i for i in data.columns if i not in ["income"]]
x_data = data[cols]
y_data = data["income"]

x_train, x_test, y_train, y_test = train_test_split(x_data, y_data, test_size=0.2, random_state=7)

In [78]:
import xgboost as xgb, lightgbm as lgbm, catboost as catb

model1 = catb.CatBoostClassifier(silent=True, random_state=21)

model1.fit(x_train, y_train)
y_predict = model1.predict(x_test)

In [79]:
from sklearn.metrics import recall_score, precision_score, roc_auc_score, accuracy_score, f1_score

def evaluate_results(y_test, y_predict):
    print('Classification results:')
    f1 = f1_score(y_test, y_predict)
    print("f1: %.2f%%" % (f1 * 100.0)) 
    roc = roc_auc_score(y_test, y_predict)
    print("roc: %.2f%%" % (roc * 100.0)) 
    rec = recall_score(y_test, y_predict, average='binary')
    print("recall: %.2f%%" % (rec * 100.0)) 
    prc = precision_score(y_test, y_predict, average='binary')
    print("precision: %.2f%%" % (prc * 100.0)) 

    
evaluate_results(y_test, y_predict)

Classification results:
f1: 71.24%
roc: 79.71%
recall: 64.85%
precision: 79.02%


### Test the PU learning approach

* Keep aside 25% of the positives -- they will be the only labeled samples

In [53]:
mod_data = data.copy()
#get the indices of the positives samples
pos_ind = np.where(mod_data["income"].values == 1)[0]
#shuffle them
np.random.shuffle(pos_ind)
# leave just 25% of the positives marked
pos_sample_len = int(np.ceil(0.25 * len(pos_ind)))
print(f'Using {pos_sample_len}/{len(pos_ind)} as positives and unlabeling the rest')
pos_sample = pos_ind[:pos_sample_len]

Using 1961/7841 as positives and unlabeling the rest


* Create the target col 'class_test' that will be 1 for postive and -1 for unlabebed¶

In [61]:
mod_data['class_test'] = -1
mod_data.loc[pos_sample,'class_test'] = 1
print('target variable:\n', mod_data.iloc[:,-1].value_counts())

target variable:
 -1    30600
 1     1961
Name: class_test, dtype: int64


In [62]:
mod_data.head()

sex  income  workclass_ ?  workclass_ Federal-gov  workclass_ Local-gov  \
0    1       0             0                       0                     0   
1    1       0             0                       0                     0   
2    1       0             0                       0                     0   
3    1       0             0                       0                     0   
4    0       0             0                       0                     0   

   workclass_ Never-worked  workclass_ Private  workclass_ Self-emp-inc  \
0                        0                   0                        0   
1                        0                   0                        0   
2                        0                   1                        0   
3                        0                   1                        0   
4                        0                   1                        0   

   workclass_ Self-emp-not-inc  workclass_ State-gov  ...  \
0                            0                     1  ...   
1                            1                     0  ...   
2                            0                     0  ...   
3                            0                     0  ...   
4                            0                     0  ...   

   hours-per-week_group_hours-per-week_41-45  \
0                                          0   
1                                          0   
2                                          0   
3                                          0   
4                                          0   

   hours-per-week_group_hours-per-week_46-50  \
0                                          0   
1                                          0   
2                                          0   
3                                          0   
4                                          0   

   hours-per-week_group_hours-per-week_51-60  \
0                                          0   
1                                          0   
2                                          0   
3                                          0   
4                                          0   

   hours-per-week_group_hours-per-week_gt_60       age    fnlwgt  \
0                                          0  0.030671 -1.063611   
1                                          0  0.837109 -1.008707   
2                                          0 -0.042642  0.245079   
3                                          0  1.057047  0.425801   
4                                          0 -0.775768  1.408176   

   capital-gain  capital-loss  hours-per-week  class_test  
0      0.148453      -0.21666       -0.035429          -1  
1     -0.145920      -0.21666       -2.222153          -1  
2     -0.145920      -0.21666       -0.035429          -1  
3     -0.145920      -0.21666       -0.035429          -1  
4     -0.145920      -0.21666       -0.035429          -1  

[5 rows x 140 columns]

In [70]:
cols = [i for i in mod_data.columns if i not in ["income","class_test"]]

x_data = mod_data[cols].values # just the X 
y_labeled = mod_data["class_test"].values # new class (just the P & U)
y_positive = mod_data["income"].values # original class

### random negative sampling

In [71]:
mod_data = mod_data.sample(frac=1)
neg_sample = mod_data[mod_data['class_test']==-1][:len(mod_data[mod_data['class_test']==1])]
sample_test = mod_data[mod_data['class_test']==-1][len(mod_data[mod_data['class_test']==1]):]
pos_sample = mod_data[mod_data['class_test']==1]
print(neg_sample.shape, pos_sample.shape)
sample_train = pd.concat([neg_sample, pos_sample]).sample(frac=1)

(1961, 140) (1961, 140)


In [72]:
cols = [i for i in mod_data.columns if i not in ["income","class_test"]]

model = catb.CatBoostClassifier(silent=True, random_state=21)

model.fit(sample_train[cols].values, 
          sample_train["income"].values)
y_predict = model.predict(sample_test[cols].values)
evaluate_results(sample_test["income"].values, y_predict)

Classification results:
f1: 60.54%
roc: 82.47%
recall: 91.08%
precision: 45.33%


In [73]:
def model_report(model,training_x,testing_x,training_y,testing_y,name) :
    model.fit(training_x,training_y)
    predictions  = model.predict(testing_x)
    accuracy     = accuracy_score(testing_y,predictions)
    recallscore  = recall_score(testing_y,predictions)
    precision    = precision_score(testing_y,predictions)
    roc_auc      = roc_auc_score(testing_y,predictions)
    f1score      = f1_score(testing_y,predictions) 
    kappa_metric = cohen_kappa_score(testing_y,predictions)
    
    df = pd.DataFrame({"Model"           : [name],
                       "Accuracy_score"  : [accuracy],
                       "Recall_score"    : [recallscore],
                       "Precision"       : [precision],
                       "f1_score"        : [f1score],
                       "Area_under_curve": [roc_auc],
                       "Kappa_metric"    : [kappa_metric],
                      })
    return df

In [81]:
from sklearn.metrics import f1_score
from sklearn.metrics import cohen_kappa_score


model_r_n_s = model_report(model,sample_train[cols].values,sample_test[cols].values,sample_train["income"].values,sample_test["income"].values,
                      "Random negative sampling")

model_usual = model_report(model1,x_train.values,x_test.values,y_train.values,y_test.values,
                      "Usual model")

model_performances = pd.concat([model_r_n_s,model_usual],axis = 0).reset_index()

model_performances = model_performances.drop(columns = "index",axis =1)

table  = ff.create_table(np.round(model_performances,4))

py.iplot(table)

**Вывод - значения не сильно ухудшились и даже ROC-AUC стала лучше**